# references
1. https://www.kaggle.com/columbia2131/device-eda-interpolate-by-removing-device-en-ja

# Load Libraries

In [1]:
import numpy as np
import pandas as pd
from glob import glob
import os
import matplotlib.pyplot as plt
from tqdm.notebook import tqdm
from pathlib import Path
import plotly.express as px

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import TensorDataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, MinMaxScaler

In [2]:
device = torch.device('cuda:0' if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


In [3]:
notebookName = 'Baseline2'
PATH = Path(f"./models/{notebookName}")

In [4]:
if os.path.isdir(PATH):
    dir_list = os.listdir(PATH)
    num_files = 0
    while True:
        if os.path.isfile(str(PATH / f"{num_files}")):
            print(num_files)
            num_files += 1
        else:
            break
else:
    os.mkdir(PATH)
    num_files = 0

In [5]:
num_files

0

# Set Hyper Parameters

In [6]:
RANDOM_STATE = 42
lr = 0.001
batch_size = 4
EPOCH_NUM = 1000


usecols = ['latDeg', 'lngDeg', 'heightAboveWgs84EllipsoidM',
             'xSatVelMps', 'ySatVelMps', 'zSatVelMps', 
             'xSatPosM', 'ySatPosM', 'zSatPosM',
            'UncalGyroXRadPerSec', 'UncalGyroYRadPerSec', 'UncalGyroZRadPerSec',
         'DriftXRadPerSec' , 'DriftYRadPerSec', 'DriftZRadPerSec',
         'UncalMagXMicroT', 'UncalMagYMicroT', 'UncalMagZMicroT',
         'UncalAccelXMps2', 'UncalAccelYMps2', 'UncalAccelZMps2']
scaled_features = ['dlatDeg', 'dlngDeg',
             'xSatVelMps', 'ySatVelMps', 'zSatVelMps', 
             'xSatPosM', 'ySatPosM', 'zSatPosM',
            'UncalGyroXRadPerSec', 'UncalGyroYRadPerSec', 'UncalGyroZRadPerSec',
         'DriftXRadPerSec' , 'DriftYRadPerSec', 'DriftZRadPerSec',
         'UncalMagXMicroT', 'UncalMagYMicroT', 'UncalMagZMicroT',
         'UncalAccelXMps2', 'UncalAccelYMps2', 'UncalAccelZMps2']
features = ['latDeg', 'lngDeg', 'heightAboveWgs84EllipsoidM',
            'dlatDeg', 'dlngDeg',
             'xSatVelMps', 'ySatVelMps', 'zSatVelMps', 
             'xSatPosM', 'ySatPosM', 'zSatPosM',
            'UncalGyroXRadPerSec', 'UncalGyroYRadPerSec', 'UncalGyroZRadPerSec',
         'DriftXRadPerSec' , 'DriftYRadPerSec', 'DriftZRadPerSec',
         'UncalMagXMicroT', 'UncalMagYMicroT', 'UncalMagZMicroT',
         'UncalAccelXMps2', 'UncalAccelYMps2', 'UncalAccelZMps2']
labels = ['t_latDeg', 't_lngDeg', 't_heightAboveWgs84EllipsoidM', 'speedMps', 'courseDegree']

In [7]:
set(features) - set(usecols)

{'dlatDeg', 'dlngDeg'}

In [8]:
torch.manual_seed(RANDOM_STATE)

experience_name = f"{num_files}"
checkpoint_name = "check_point"
model_name = str("model - " + experience_name)
param_name = str("param - " + experience_name)
result_name = str("result - " + experience_name)

dummy_path = str(PATH / f"{num_files}")
checkpoint_path = str(PATH / f"{checkpoint_name}.pth")
model_path = str(PATH / f"{model_name}.pth")
param_path = str(PATH / f"{param_name}.pth")
result_path = str(PATH / f"{result_name}.csv")
model_path, param_path, result_path

('models\\Baseline2\\model - 0.pth',
 'models\\Baseline2\\param - 0.pth',
 'models\\Baseline2\\result - 0.csv')

# Useful Functions

In [9]:
def calc_haversine(lat1, lon1, lat2, lon2):
    dlat = (lat2 - lat1) % 360
    dlon = (lon2 - lon1) % 360 
    
    dlat, dlon = map(np.radians, [dlat, dlon])
    a = np.sin(dlat / 2.0)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2.0)**2
    c = 2 * np.arcsin(a ** 0.5)
        
    dist = 6_367_000 * c
    return dist

In [10]:
def check_score(input_df: pd.DataFrame) -> pd.DataFrame:
    output_df = input_df.copy()
    
    output_df['meter'] = input_df.apply(
        lambda r: calc_haversine(
            r.latDeg, r.lngDeg, r.t_latDeg, r.t_lngDeg
        ),
        axis=1
    )

    meter_score = output_df['meter'].mean()
    print(f'error meter: {meter_score}')

    scores = []
    for phone in output_df['phone'].unique():
        _index = output_df['phone']==phone
        p_50 = np.percentile(output_df.loc[_index, 'meter'], 50)
        p_95 = np.percentile(output_df.loc[_index, 'meter'], 95)
        scores.append(p_50)
        scores.append(p_95)

    score = sum(scores) / len(scores)
    print(f'score: {score}')
    
    return output_df, meter_score , score

In [11]:
def check_score_np(predict:torch.Tensor, target:torch.Tensor):
    m = []
    predict = predict.detach().numpy()
    target = target.detach().numpy()
    for i in range(predict.shape[0]):
        temp = calc_haversine(predict[i,0], predict[i,1], target[i,0], target[i,1])
        m.append(temp)
    
    m = np.array(m)
    score = (np.percentile(m, 50) + np.percentile(m, 95))/2
    
    return score

# Load Datasets

In [12]:
data_dir = Path("../input/google-smartphone-decimeter-challenge")
df_train = pd.read_pickle(str(data_dir / "gsdc_train.pkl.gzip"))

In [13]:
# check score
df_train, default_loss, default_meas = check_score(df_train)

error meter: 4.261468362435763
score: 5.812326742270749


# Feature Engineering
## Simple view, what is in data frame.

In [14]:
print(df_train.shape)
df_train.head()

(131342, 111)


collectionName       phoneName  millisSinceGpsEpoch     latDeg  \
0  2020-05-14-US-MTV-1          Pixel4        1273529463442  37.423575   
1  2020-05-14-US-MTV-1          Pixel4        1273529464442  37.423578   
2  2020-05-14-US-MTV-1          Pixel4        1273529465442  37.423573   
3  2020-05-14-US-MTV-1          Pixel4        1273529466442  37.423583   
4  2020-05-14-US-MTV-1  Pixel4XLModded        1273529466449  37.423574   

       lngDeg  heightAboveWgs84EllipsoidM                               phone  \
0 -122.094091                      -34.06          2020-05-14-US-MTV-1_Pixel4   
1 -122.094101                      -33.29          2020-05-14-US-MTV-1_Pixel4   
2 -122.094111                      -30.99          2020-05-14-US-MTV-1_Pixel4   
3 -122.094121                      -32.83          2020-05-14-US-MTV-1_Pixel4   
4 -122.094137                      -33.20  2020-05-14-US-MTV-1_Pixel4XLModded   

   utcTimeMillis_x  elapsedRealtimeNanos_x  UncalGyroXRadPerSec  ...  \
0     1.589494e+12            1.965654e+13            -0.000502  ...   
1     1.589494e+12            1.965754e+13            -0.003537  ...   
2     1.589494e+12            1.965854e+13             0.002028  ...   
3     1.589494e+12            1.965954e+13            -0.015753  ...   
4     1.589494e+12            1.734189e+13             0.875268  ...   

   ySatVelMps  zSatVelMps  satClkBiasM  satClkDriftMps        rawPrM  \
0     156.040    3559.757     -468.084           0.001  2.379498e+07   
1     411.162   -3013.649    65954.431          -0.002  2.592442e+07   
2   -2776.605    -434.445     1223.261           0.000  2.131445e+07   
3     411.755   -3013.528    65954.426          -0.002  2.592544e+07   
4     -81.334   -3057.885    -3909.257           0.001  2.318871e+07   

   rawPrUncM     isrbM  ionoDelayM  tropoDelayM     meter  
0     11.992  1134.758      10.866       16.647  4.345847  
1      3.897  -222.675       7.111        5.174  3.324526  
2      1.499     0.000       4.777        3.371  2.279173  
3      3.598  -220.611       7.113        5.183  1.381411  
4     10.493     0.000       7.313        5.311  0.794351  

[5 rows x 111 columns]

In [15]:
for c in df_train.columns:
    print(c)
    print(df_train[c].describe())
    print()

collectionName
count                  131342
unique                     29
top       2021-01-04-US-RWC-1
freq                     8293
Name: collectionName, dtype: object

phoneName
count     131342
unique         7
top       Pixel4
freq       48153
Name: phoneName, dtype: object

millisSinceGpsEpoch
count    1.313420e+05
mean     1.287913e+12
std      1.162110e+10
min      1.273529e+12
25%      1.275424e+12
50%      1.283279e+12
75%      1.302558e+12
max      1.303771e+12
Name: millisSinceGpsEpoch, dtype: float64

latDeg
count    131342.000000
mean         37.435206
std           0.082712
min          37.321683
25%          37.371575
50%          37.424360
75%          37.469109
max          37.690836
Name: latDeg, dtype: float64

lngDeg
count    131342.000000
mean       -122.154925
std           0.145974
min        -122.472214
25%        -122.275109
50%        -122.118311
75%        -122.069091
max        -121.881855
Name: lngDeg, dtype: float64

heightAboveWgs84EllipsoidM
count    1

Name: DriftUncertaintyNanosPerSecond, dtype: float64

HardwareClockDiscontinuityCount
count    131342.000000
mean        904.863547
std        2067.940289
min           0.000000
25%           1.000000
50%           8.000000
75%         932.000000
max       12484.000000
Name: HardwareClockDiscontinuityCount, dtype: float64

Svid_x
count    131342.000000
mean         21.857091
std          26.931186
min           1.000000
25%           9.000000
50%          19.000000
75%          27.000000
max         195.000000
Name: Svid_x, dtype: float64

TimeOffsetNanos
count    131342.0
mean          0.0
std           0.0
min           0.0
25%           0.0
50%           0.0
75%           0.0
max           0.0
Name: TimeOffsetNanos, dtype: float64

State
count    131342.000000
mean      37819.338597
std       27131.543312
min           4.000000
25%       16399.000000
50%       23567.000000
75%       49359.000000
max       85034.000000
Name: State, dtype: float64

ReceivedSvTimeNanos
count    1.31342

count    36572.000000
mean       -61.415017
std         34.612914
min        -89.000000
25%        -84.000000
50%        -81.000000
75%        -45.000000
max         21.000000
Name: pitchDeg, dtype: float64

timeSinceFirstFixSeconds
count    131342.000000
mean       1213.986316
std         609.145524
min          47.430000
25%         718.430000
50%        1174.430000
75%        1659.440000
max        3216.450000
Name: timeSinceFirstFixSeconds, dtype: float64

hDop
count    131342.000000
mean         10.146238
std          56.707267
min           0.000000
25%           0.900000
50%           1.300000
75%           2.500000
max         655.300000
Name: hDop, dtype: float64

vDop
count    131342.0
mean          0.0
std           0.0
min           0.0
25%           0.0
50%           0.0
75%           0.0
max           0.0
Name: vDop, dtype: float64

speedMps
count    131342.000000
mean         18.220691
std          12.698756
min           0.000000
25%           5.260000
50%          22.0

In [16]:
for col in df_train.columns:
    print(col)

collectionName
phoneName
millisSinceGpsEpoch
latDeg
lngDeg
heightAboveWgs84EllipsoidM
phone
utcTimeMillis_x
elapsedRealtimeNanos_x
UncalGyroXRadPerSec
UncalGyroYRadPerSec
UncalGyroZRadPerSec
DriftXRadPerSec
DriftYRadPerSec
DriftZRadPerSec
utcTimeMillis_y
elapsedRealtimeNanos_y
UncalMagXMicroT
UncalMagYMicroT
UncalMagZMicroT
BiasXMicroT
BiasYMicroT
BiasZMicroT
utcTimeMillis_x
TimeNanos
LeapSecond
TimeUncertaintyNanos
FullBiasNanos
BiasNanos
BiasUncertaintyNanos
DriftNanosPerSecond
DriftUncertaintyNanosPerSecond
HardwareClockDiscontinuityCount
Svid_x
TimeOffsetNanos
State
ReceivedSvTimeNanos
ReceivedSvTimeUncertaintyNanos
Cn0DbHz_x
PseudorangeRateMetersPerSecond
PseudorangeRateUncertaintyMetersPerSecond
AccumulatedDeltaRangeState
AccumulatedDeltaRangeMeters
AccumulatedDeltaRangeUncertaintyMeters
CarrierFrequencyHz_x
CarrierCycles
CarrierPhase
CarrierPhaseUncertainty
MultipathIndicator
SnrInDb
ConstellationType_x
AgcDb
BasebandCn0DbHz_x
FullInterSignalBiasNanos
FullInterSignalBiasUncertai

## Feature Extractor

In [37]:
def FeatureExtraction(df:pd.DataFrame, use_cols, features) -> pd.DataFrame:
    output = df.copy()
    need_create_features = set(features) - set(use_cols)
    
    for needy in features:
        if needy in ['dlatDeg', 'dlngDeg']:
            output[needy] = DeltaLatLong(output, needy)
        elif needy == 'DriftXRadPerSec':
            output[needy] = WrongDataTypeStrDriftXRadPerSec(output, needy)
    
    return output

def WrongDataTypeStrDriftXRadPerSec(df:pd.DataFrame, col):
    output = df.copy()
    for i in (range(df.shape[0])):
        x = output.iloc[i][col]
        if type(x) != float:
            if type(x) == str and x[-1] == 'E':
                x = x + '-4'
            x_ = x
            x = float(x)
            print(type(x_), x, type(x), x)
            output.iloc[i][col] = x
    return output[col]
    
def DeltaLatLong(df:pd.DataFrame, col):
    output = df.copy()
    output[col] = 0
    if col == 'dlatDeg':
        target = 'latDeg'
    else:
        target = 'lngDeg'
        
    for phone in output['phone'].unique():
        temp = output[output['phone'] == phone]
        origin = temp.reset_index().iloc[0][target]
        output.loc[output['phone'] == phone,col] = temp[target] - origin
    
    return output[col]

df_train = FeatureExtraction(df_train, usecols, features)
print(df_train.columns)
df_train.head()

<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'floa

D:\Sangwons_Room\00_SoftWares\Anaconda\envs\torch\lib\site-packages\ipykernel_launcher.py:23: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



 nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.f

<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'floa

<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'float'> nan
<class 'numpy.float64'> nan <class 'floa

...

<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0005508283 <class 'float'> -0.0005508283
<class 'numpy.float64'> 8.068915e-05 <class 'float'> 8.068915e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0005508283 <class 'float'> -0.0005508283
<class 'numpy.float64'> 8.068915e-05 <class 'float'> 8.068915e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0005509425 <class 'float'> -0.0005509425
<class 'numpy.float64'> 8.068915e-05 <class 'float'> 8.068915e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0005507141 <class 'float'> -0.0005507141
<class 'numpy.float64'> 8.068915e-05 <class 'float'> 8.068915e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00055014325 <class 'float'> -0.00055014325
<class 'numpy.float64'> 8.068915e-05 <class 'float'> 8

<class 'numpy.float64'> -0.00038444038 <class 'float'> -0.00038444038
<class 'numpy.float64'> 5.7145113e-05 <class 'float'> 5.7145113e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00038444033 <class 'float'> -0.00038444033
<class 'numpy.float64'> 5.7145113e-05 <class 'float'> 5.7145113e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0003843251 <class 'float'> -0.0003843251
<class 'numpy.float64'> 0.000104438004 <class 'float'> 0.000104438004
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00041684858 <class 'float'> -0.00041684858
<class 'numpy.float64'> 8.473270000000001e-05 <class 'float'> 8.473270000000001e-05
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0005000619 <class 'float'> -0.0005000619
<class 'numpy.float64'> 8.473270000000001e-05 <class 'float'> 8.473270000000001e-05
<class '

<class 'numpy.float64'> 0.00010111590399999999 <class 'float'> 0.00010111590399999999
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0002152543 <class 'float'> -0.0002152543
<class 'numpy.float64'> 0.00010111590399999999 <class 'float'> 0.00010111590399999999
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00021473411 <class 'float'> -0.00021473411
<class 'numpy.float64'> 0.00010111590399999999 <class 'float'> 0.00010111590399999999
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00021464741 <class 'float'> -0.00021464741
<class 'numpy.float64'> 0.00010111590399999999 <class 'float'> 0.00010111590399999999
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00021542769 <class 'float'> -0.00021542769
<class 'numpy.float64'> 0.00010111590399999999 <class 'float'> 0.00010111590399999999
<class 'numpy.float6

<class 'numpy.float64'> -0.00021043707000000002 <class 'float'> -0.00021043707000000002
<class 'numpy.float64'> 0.00010504691500000001 <class 'float'> 0.00010504691500000001
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.0002104804 <class 'float'> -0.0002104804
<class 'numpy.float64'> 0.00010386927 <class 'float'> 0.00010386927
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00021052377000000002 <class 'float'> -0.00021052377000000002
<class 'numpy.float64'> 0.00010386927 <class 'float'> 0.00010386927
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00021065382000000002 <class 'float'> -0.00021065382000000002
<class 'numpy.float64'> 0.00010386927 <class 'float'> 0.00010386927
<class 'numpy.float64'> -0.0005027421 <class 'float'> -0.0005027421
<class 'numpy.float64'> -0.00021030159 <class 'float'> -0.00021030159
<class 'numpy.float64'> 0.0001038692

collectionName       phoneName  millisSinceGpsEpoch     latDeg  \
0  2020-05-14-US-MTV-1          Pixel4        1273529463442  37.423575   
1  2020-05-14-US-MTV-1          Pixel4        1273529464442  37.423578   
2  2020-05-14-US-MTV-1          Pixel4        1273529465442  37.423573   
3  2020-05-14-US-MTV-1          Pixel4        1273529466442  37.423583   
4  2020-05-14-US-MTV-1  Pixel4XLModded        1273529466449  37.423574   

       lngDeg  heightAboveWgs84EllipsoidM                               phone  \
0 -122.094091                      -34.06          2020-05-14-US-MTV-1_Pixel4   
1 -122.094101                      -33.29          2020-05-14-US-MTV-1_Pixel4   
2 -122.094111                      -30.99          2020-05-14-US-MTV-1_Pixel4   
3 -122.094121                      -32.83          2020-05-14-US-MTV-1_Pixel4   
4 -122.094137                      -33.20  2020-05-14-US-MTV-1_Pixel4XLModded   

   utcTimeMillis_x  elapsedRealtimeNanos_x  UncalGyroXRadPerSec  ...  \
0     1.589494e+12            1.965654e+13            -0.000502  ...   
1     1.589494e+12            1.965754e+13            -0.003537  ...   
2     1.589494e+12            1.965854e+13             0.002028  ...   
3     1.589494e+12            1.965954e+13            -0.015753  ...   
4     1.589494e+12            1.734189e+13             0.875268  ...   

   satClkBiasM  satClkDriftMps        rawPrM  rawPrUncM     isrbM  ionoDelayM  \
0     -468.084           0.001  2.379498e+07     11.992  1134.758      10.866   
1    65954.431          -0.002  2.592442e+07      3.897  -222.675       7.111   
2     1223.261           0.000  2.131445e+07      1.499     0.000       4.777   
3    65954.426          -0.002  2.592544e+07      3.598  -220.611       7.113   
4    -3909.257           0.001  2.318871e+07     10.493     0.000       7.313   

   tropoDelayM     meter  dlngDeg   dlatDeg  
0       16.647  4.345847  0.00000  0.000000  
1        5.174  3.324526 -0.00001  0.000002  
2        3.371  2.279173 -0.00002 -0.000002  
3        5.183  1.381411 -0.00003  0.000007  
4        5.311  0.794351  0.00000  0.000000  

[5 rows x 113 columns]

In [38]:
df_ = FeatureExtraction(df_test, usecols, features)
for v in df_['DriftXRadPerSec']:
    if  type(v) == float or  type(v) == int:
        pass
    else:
        print(type(v), v)

<class 'str'> -0.0007093253 <class 'float'> -0.0007093253
<class 'str'> -0.0007088188 <class 'float'> -0.0007088188
<class 'str'> -0.0007074449 <class 'float'> -0.0007074449
<class 'str'> -0.0007067865 <class 'float'> -0.0007067865
<class 'str'> -0.00070526707 <class 'float'> -0.00070526707
<class 'str'> -0.0007050138 <class 'float'> -0.0007050138
<class 'str'> -0.00070511515 <class 'float'> -0.00070511515
<class 'str'> -0.00070511515 <class 'float'> -0.00070511515
<class 'str'> -0.0007062294 <class 'float'> -0.0007062294
<class 'str'> -0.00070648274 <class 'float'> -0.00070648274
<class 'str'> -0.0007068879 <class 'float'> -0.0007068879
<class 'str'> -0.00070703984 <class 'float'> -0.00070703984
<class 'str'> -0.000706432 <class 'float'> -0.000706432
<class 'str'> -0.0007067866 <class 'float'> -0.0007067866
<class 'str'> -0.000706584 <class 'float'> -0.000706584
<class 'str'> -0.00070638146 <class 'float'> -0.00070638146
<class 'str'> -0.00070638146 <class 'float'> -0.00070638146
<cla

D:\Sangwons_Room\00_SoftWares\Anaconda\envs\torch\lib\site-packages\ipykernel_launcher.py:23: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



 -0.0006986952 <class 'float'> -0.0006986952
<class 'str'> -0.00069857243 <class 'float'> -0.00069857243
<class 'str'> -0.0006987361 <class 'float'> -0.0006987361
<class 'str'> -0.0006993141 <class 'float'> -0.0006993141
<class 'str'> -0.00069939595 <class 'float'> -0.00069939595
<class 'str'> -0.00069939595 <class 'float'> -0.00069939595
<class 'str'> -0.0006994778 <class 'float'> -0.0006994778
<class 'str'> -0.00069955963 <class 'float'> -0.00069955963
<class 'str'> -0.00069980515 <class 'float'> -0.00069980515
<class 'str'> -0.0006997233 <class 'float'> -0.0006997233
<class 'str'> -0.00069964153 <class 'float'> -0.00069964153
<class 'str'> -0.00069947785 <class 'float'> -0.00069947785
<class 'str'> -0.0006999688 <class 'float'> -0.0006999688
<class 'str'> -0.0006999688 <class 'float'> -0.0006999688
<class 'str'> -0.0006999688 <class 'float'> -0.0006999688
<class 'str'> -0.000699887 <class 'float'> -0.000699887
<class 'str'> -0.0007001325 <class 'float'> -0.0007001325
<class 'str'> -

<class 'str'> -0.00071857416 <class 'float'> -0.00071857416
<class 'str'> -0.00071824685 <class 'float'> -0.00071824685
<class 'str'> -0.00071824685 <class 'float'> -0.00071824685
<class 'str'> -0.0007184924 <class 'float'> -0.0007184924
<class 'str'> -0.00071795535 <class 'float'> -0.00071795535
<class 'str'> -0.0007184924 <class 'float'> -0.0007184924
<class 'str'> -0.0007184924 <class 'float'> -0.0007184924
<class 'str'> -0.0007187379 <class 'float'> -0.0007187379
<class 'str'> -0.00071869703 <class 'float'> -0.00071869703
<class 'str'> -0.0007189016 <class 'float'> -0.0007189016
<class 'str'> -0.0007189016 <class 'float'> -0.0007189016
<class 'str'> -0.0007189016 <class 'float'> -0.0007189016
<class 'str'> -0.0007192289 <class 'float'> -0.0007192289
<class 'str'> -0.00071906525 <class 'float'> -0.00071906525
<class 'str'> -0.0007191471 <class 'float'> -0.0007191471
<class 'str'> -0.00071939256 <class 'float'> -0.00071939256
<class 'str'> -0.00071890163 <class 'float'> -0.0007189016

<class 'str'> -0.0007116448 <class 'float'> -0.0007116448
<class 'str'> -0.0007116448 <class 'float'> -0.0007116448
<class 'str'> -0.00071189535 <class 'float'> -0.00071189535
<class 'str'> -0.00071189535 <class 'float'> -0.00071189535
<class 'str'> -0.0007113583 <class 'float'> -0.0007113583
<class 'str'> -0.0007113583 <class 'float'> -0.0007113583
<class 'str'> -0.0007109492 <class 'float'> -0.0007109492
<class 'str'> -0.0007111128 <class 'float'> -0.0007111128
<class 'str'> -0.0007111128 <class 'float'> -0.0007111128
<class 'str'> -0.00071086735 <class 'float'> -0.00071086735
<class 'str'> -0.0007106218 <class 'float'> -0.0007106218
<class 'str'> -0.0007106218 <class 'float'> -0.0007106218
<class 'str'> -0.0007109082 <class 'float'> -0.0007109082
<class 'str'> -0.0007103763 <class 'float'> -0.0007103763
<class 'str'> -0.00071082637 <class 'float'> -0.00071082637
<class 'str'> -0.00071054 <class 'float'> -0.00071054
<class 'str'> -0.00071078545 <class 'float'> -0.00071078545
<class '

<class 'str'> -0.000741125 <class 'float'> -0.000741125
<class 'str'> -0.0007407977 <class 'float'> -0.0007407977
<class 'str'> -0.0007419433 <class 'float'> -0.0007419433
<class 'str'> -0.0007417387 <class 'float'> -0.0007417387
<class 'str'> -0.0007429304 <class 'float'> -0.0007429304
<class 'str'> -0.00074333954 <class 'float'> -0.00074333954
<class 'str'> -0.00074325775 <class 'float'> -0.00074325775
<class 'str'> -0.00074325775 <class 'float'> -0.00074325775
<class 'str'> -0.0007440351 <class 'float'> -0.0007440351
<class 'str'> -0.00074518076 <class 'float'> -0.00074518076
<class 'str'> -0.0007455899 <class 'float'> -0.0007455899
<class 'str'> -0.0007458814 <class 'float'> -0.0007458814
<class 'str'> -0.0007456308 <class 'float'> -0.0007456308
<class 'str'> -0.0007455899 <class 'float'> -0.0007455899
<class 'str'> -0.0007453444 <class 'float'> -0.0007453444
<class 'str'> -0.0007460451 <class 'float'> -0.0007460451
<class 'str'> -0.0007458405 <class 'float'> -0.0007458405
<class '

<class 'str'> -0.0006938815 <class 'float'> -0.0006938815
<class 'str'> -0.00069359504 <class 'float'> -0.00069359504
<class 'str'> -0.0006935542 <class 'float'> -0.0006935542
<class 'str'> -0.00069347234 <class 'float'> -0.00069347234
<class 'str'> -0.0006940861 <class 'float'> -0.0006940861
<class 'str'> -0.00069379964 <class 'float'> -0.00069379964
<class 'str'> -0.0006933905 <class 'float'> -0.0006933905
<class 'str'> -0.000693145 <class 'float'> -0.000693145
<class 'str'> -0.00069330866 <class 'float'> -0.00069330866
<class 'str'> -0.0006928177 <class 'float'> -0.0006928177
<class 'str'> -0.0006923267 <class 'float'> -0.0006923267
<class 'str'> -0.0006928995 <class 'float'> -0.0006928995
<class 'str'> -0.0006928995 <class 'float'> -0.0006928995
<class 'str'> -0.0006937178 <class 'float'> -0.0006937178
<class 'str'> -0.0006941679 <class 'float'> -0.0006941679
<class 'str'> -0.0006938815 <class 'float'> -0.0006938815
<class 'str'> -0.0006941679 <class 'float'> -0.0006941679
<class '

<class 'str'> -0.00069490436 <class 'float'> -0.00069490436
<class 'str'> -0.0006947407 <class 'float'> -0.0006947407
<class 'str'> -0.0006947407 <class 'float'> -0.0006947407
<class 'str'> -0.00069449516 <class 'float'> -0.00069449516
<class 'str'> -0.0006947407 <class 'float'> -0.0006947407
<class 'str'> -0.0006949862 <class 'float'> -0.0006949862
<class 'str'> -0.0006949862 <class 'float'> -0.0006949862
<class 'str'> -0.00069519074 <class 'float'> -0.00069519074
<class 'str'> -0.00069457706 <class 'float'> -0.00069457706
<class 'str'> -0.00069465884 <class 'float'> -0.00069465884
<class 'str'> -0.00069465884 <class 'float'> -0.00069465884
<class 'str'> -0.00069465884 <class 'float'> -0.00069465884
<class 'str'> -0.00069449516 <class 'float'> -0.00069449516
<class 'str'> -0.0006948225 <class 'float'> -0.0006948225
<class 'str'> -0.0006943316 <class 'float'> -0.0006943316
<class 'str'> -0.0006944133 <class 'float'> -0.0006944133
<class 'str'> -0.00069424976 <class 'float'> -0.00069424

<class 'str'> -6.9457706E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.9449516E-4
<class 'str'> -6.944133E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9490436E-4
<class 'str'> -6.9449516E-4
<class 'str'> -6.948225E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.944133E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9490436E-4
<class 'str'> -6.9519074E-4
<class 'str'> -6.949862E-4
<class 'str'> -6.9506804E-4
<class 'str'> -6.951089E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9490436E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.9449516E-4
<class 'str'> -6.947407E-4
<class 'str'> -6.949862E-4
<class 'str'> -6.949862E-4
<class 'str'> -6.9519074E-4
<class 'str'> -6.9457706E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9465884E-4
<class 'str'> -6.9449516E-4
<class 'str'> -6.948225E-4
<class 

## Create Scaler Class

In [ ]:
class Scaler():
    def __init__(self, data, cols):
        self.scaler = dict()
        for col in cols:
            self.scaler[col] = MinMaxScaler()
            self.scaler[col].fit(self.to_numpy(data[col]))
    def transform(self, data):
        output = data.copy()
        keys = self.scaler.keys()
        for col in output.columns:
            if col in keys:
                temp = self.scaler[col].transform(self.to_numpy(data[col]))
                output[col] = self.to_series(temp, col)
        return output
    
    def inverse_transform(self, data):
        output = data.copy()
        keys = self.scaler.keys()
        for col in output.columns:
            if col in keys:
                output[col] = self.scaler[col].inverse_transform(output[col])
        return output
    def to_numpy(self, series):
        return np.array(series).reshape(-1, 1)
        
    def to_series(self, array, col):
        array = array.reshape(-1)
        return pd.Series(data = array, name = col)
        
        
            
scaler = Scaler(df_train, scaled_features)
df_train = scaler.transform(df_train)
df_train

In [ ]:
df_train[features].info()

In [ ]:
df_train = df_train.fillna(method = 'pad')
df_train = df_train.fillna(0)

In [ ]:
df_train[features].describe()

In [ ]:
def data_slice_by_phone(df:pd.DataFrame, 
                        xCols = ['latDeg', 'lngDeg', 'heightAboveWgs84EllipsoidM'], 
                        yCols = ['t_latDeg', 't_lngDeg', 't_heightAboveWgs84EllipsoidM', 'speedMps', 'courseDegree']):
    indexCols = ['collectionName', 'phoneName', 'millisSinceGpsEpoch']
    
    indx = []
    data = []
    true = []
    for i, phone in enumerate(df['phone'].unique()):
        temp = df[df['phone'] == phone]
        indx.append(temp[indexCols])
        data.append(temp[xCols])
        true.append(temp[yCols])
        
    return indx, data, true

def data_merge_by_index(df:pd.DataFrame, index:pd.DataFrame, src:pd.DataFrame, srcCols = ['latDeg', 'lngDeg', 'heightAboveWgs84EllipsoidM']):
    indexCols = ['collectionName', 'phoneName', 'millisSinceGpsEpoch']
    output = df.copy()
    
    listFrame = []
    for i in range(len(index)):
        idxFrame = index[i]
        srcFrame = src[i]
        temp = pd.concat([idxFrame, srcFrame], axis = 1)
        listFrame.append(temp)
    
    dataFrame = pd.concat(listFrame, axis = 0)
    output = output.merge(dataFrame,
              on=["collectionName", "phoneName", "millisSinceGpsEpoch"])
    
    return output

idxFrame, dataFrame, trueFrame = data_slice_by_phone(df_train, xCols=features, yCols = labels)

# Check!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
slide window 기반은 때려치고, 데이터프레임에서 직접 읽어오는 방식으로 변경할 필요가 있음
collectionName, phoneName기반으로 데이터를 잘라서 시계열 데이터처럼 쓸 예정 우선적으로 필요한 것은 lstm으로 돌려보기(baseline을 그렇게 하자!)

# Modeling

In [ ]:
# build model
class ConvBlock(nn.Module):
    def __init__(self, input_features, output_features, kernel_size = 3):
        super().__init__()
        
        self.convK = nn.Conv1d(input_features, output_features, kernel_size = kernel_size, padding = kernel_size//2)
        self.conv = nn.Conv1d(input_features, output_features, 1)
        self.bn = nn.BatchNorm1d(output_features)
        
    def forward(self, inputs):
        x = self.convK(inputs)
        inputs = self.conv(inputs)
        x = self.bn(x)
        x = F.relu(x)
        outputs = x + inputs
        return outputs
    
class BigConv(nn.Module):
    def __init__(self, input_size, output_size):
        super().__init__()
        self.conv1 = ConvBlock(input_size, 2*input_size)
        self.conv2 = ConvBlock(2*input_size, 4*input_size)
        self.conv3 = ConvBlock(4*input_size, 4*input_size)
        self.conv4 = ConvBlock(4*input_size, 4*input_size)
        self.conv5 = ConvBlock(4*input_size, output_size)
        
    def forward(self, x):
        x = self.conv1(x)
        x = self.conv2(x)
        x = self.conv3(x)
        x = self.conv4(x)
        x = self.conv5(x)
        return x
    
    
    
class ConvolutionNetwork(nn.Module):
    def __init__(self, input_size, output_size):
        super().__init__()
        
#         self.conv = nn.Conv1d(input_size, output_size, 1)
        self.conv1 = BigConv(input_size, 64)
        self.conv2 = BigConv(64, 64)
        self.conv3 = BigConv(64, 64)
        self.conv4 = BigConv(64, output_size)
        
#         self.lstm = nn.LSTM(input_size = 512 + output_size, hidden_size = output_size, num_layers = 3, dropout = 0.3)
    
    def forward(self, x):
#         x1 = self.conv(x)
        
        x = self.conv1(x)
        x = self.conv2(x)
        x = self.conv3(x)
        x = self.conv4(x)
        
#         x = torch.cat([x1, x], axis = 1)
#         x, hidden = self.lstm(x)
        
        return x
    
model = ConvolutionNetwork(len(features), len(labels))
model.to(device)

# loss_func = nn.SmoothL1Loss()
loss_func = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr = lr)
scheduler = optim.lr_scheduler.LambdaLR(optimizer=optimizer,
                                lr_lambda=lambda epoch: 0.995 ** epoch,
                                last_epoch=-1,
                                verbose=True)

In [ ]:
class CustomDataloader(torch.utils.data.Dataset):
    def __init__(self, data, true = None):
        self.data = data
        self.true = true
        self.len = len(data)
        
    
    def __len__(self):
        return self.len
    
    def __shuffle__(self):
        index = np.array(range(self.len), dtype = 'int')
        index = np.random.permutation(index)
        data = []
        true = []
        for i in range(self.len):
            data.append(self.data[index[i]])
            true.append(self.true[index[i]])
            
        self.data = data
        self.true = true
    
    def __getitem__(self, idx):
        data = self.data[idx]
        if self.true is None:
            true = []
        else:
            true = self.true[idx]
            
        data = torch.Tensor(np.expand_dims(np.array(data), 0)).transpose(2, 1)
        true = torch.Tensor(np.expand_dims(np.array(true), 0)).transpose(2, 1)
        
        return data, true
    

In [ ]:
Xtrain, Xtest, ytrain, ytest = train_test_split(dataFrame, trueFrame, test_size = 1/10)

loader_train = CustomDataloader(Xtrain, ytrain)
loader_test = CustomDataloader(Xtest, ytest)

In [ ]:
def train(epoch):
    model.train()  # 신경망을 학습 모드로 전환

    # 데이터로더에서 미니배치를 하나씩 꺼내 학습을 수행
    predict = []
    ground = []
    
    loader_train.__shuffle__()
    
    for data, targets in loader_train:
        
        data = data.to(device)
        targets = targets.to(device)
        
        optimizer.zero_grad()  # 경사를 0으로 초기화
        outputs = model(data)  # 데이터를 입력하고 출력을 계산
        loss = loss_func(outputs, targets)  # 출력과 훈련 데이터 정답 간의 오차를 계산
        loss.backward()  # 오차를 역전파 계산
        optimizer.step()  # 역전파 계산한 값으로 가중치를 수정
        
        predict.append(outputs.squeeze(dim = 0).transpose(1,0))
        ground.append(targets.squeeze(dim = 0).transpose(1,0))
    scheduler.step()

    # 정확도 출력
    predict = torch.cat(predict,axis = 0)
    ground = torch.cat(ground,axis = 0)
    
    loss = loss_func(predict, ground)
    meas = check_score_np(predict.to('cpu'), ground.to('cpu'))
    return loss, meas

In [ ]:
def test():
    model.eval()  # 신경망을 추론 모드로 전환

    # 데이터로더에서 미니배치를 하나씩 꺼내 추론을 수행
    predict = []
    ground = []
    with torch.no_grad():  # 추론 과정에는 미분이 필요없음
        for data, targets in loader_test:
            data = data.to(device)
            targets = targets.to(device)
            
            outputs = model(data)  # 데이터를 입력하고 출력을 계산
            predict.append(outputs.squeeze(dim = 0).transpose(1,0))
            ground.append(targets.squeeze(dim = 0).transpose(1,0))

    # 정확도 출력
    predict = torch.cat(predict,axis = 0)
    ground = torch.cat(ground,axis = 0)
    
    loss = loss_func(predict, ground)
    meas = check_score_np(predict.to('cpu'), ground.to('cpu'))
    return loss, meas

In [ ]:
test()

In [ ]:
history = []
train_loss, train_meas = 0,0
test_loss, test_meas = 0,0

check_meas = np.inf
check_loss = np.inf
check_epoch = 0

for epoch in range(EPOCH_NUM+1):
    if epoch != 0:
        train_loss, train_meas = train(epoch)
    test_loss, test_meas = test()
    
    history.append({'epoch':epoch, 'train_loss':train_loss, 'train_meas':train_meas, 'test_loss':test_loss, 'test_meas':test_meas})
    
    if (test_meas < check_meas):
        print("")
        print(f"/***CHECK_POINT***/ ")
        print(f"TRAIN - {train_loss}, {train_meas}")
        print(f"TEST - {test_loss}, {test_meas}")
        print("")
        check_meas = test_meas
        check_loss = test_loss
        check_epoch = epoch
        torch.save(model.state_dict(), checkpoint_path)
    
    print(f"/*** EPOCH : {epoch}/{EPOCH_NUM} ***/")
    print(f"TRAIN - {train_loss}, {train_meas}")
    print(f"TEST - {test_loss}, {test_meas}")
    print("")
    
df_history = pd.DataFrame(history)

In [ ]:
df_history = pd.DataFrame(history)

fig, axes = plt.subplots(2,1,figsize = (8,12))

axes[0].plot(df_history['epoch'], df_history['train_loss'])
axes[0].plot(df_history['epoch'], df_history['test_loss'])
axes[0].axvline(x = check_epoch, ymin = 0, ymax = df_history['test_loss'].max(), color = 'r')
axes[0].axhline(y = default_loss, xmin = 0, xmax = df_history['epoch'].max(), color = 'k')
axes[0].set_ylim(0, 5000)

axes[1].plot(df_history['epoch'], df_history['train_meas'])
axes[1].plot(df_history['epoch'], df_history['test_meas'])
axes[1].axvline(x = check_epoch, ymin = 0, ymax = df_history['test_meas'].max(), color = 'r')
axes[1].axhline(y = default_meas, xmin = 0, xmax = df_history['epoch'].max(), color = 'k')

In [ ]:
del X_train, X_test, y_train, y_test

# Submission

In [21]:
df_test = pd.read_pickle(str(data_dir / "gsdc_test.pkl.gzip"))

In [22]:
df_test = FeatureExtraction(df_test, usecols, features)
df_test.info(verbose = True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 91486 entries, 0 to 91485
Data columns (total 104 columns):
 #   Column                                     Dtype  
---  ------                                     -----  
 0   collectionName                             object 
 1   phoneName                                  object 
 2   millisSinceGpsEpoch                        int64  
 3   latDeg                                     float64
 4   lngDeg                                     float64
 5   heightAboveWgs84EllipsoidM                 float64
 6   phone                                      object 
 7   utcTimeMillis_x                            float64
 8   elapsedRealtimeNanos_x                     float64
 9   UncalGyroXRadPerSec                        float64
 10  UncalGyroYRadPerSec                        float64
 11  UncalGyroZRadPerSec                        float64
 12  DriftXRadPerSec                            object 
 13  DriftYRadPerSec                            fl

In [ ]:
df_test = df_test.fillna(method = 'pad')
df_test = df_test.fillna(0)

In [ ]:
for col, s in scaler.scaler.items():
    print(col)
    print(df_test[col])
    print(s.transform(np.array(df_test[col]).reshape(-1,1)))

In [20]:
for v in df_test[col]:
    if  type(v) == float or  type(v) == int:
        pass
    else:
        print(type(v), v)

NameError: name 'df_test' is not defined

In [ ]:

df_test = scaler.transform(df_test)

print(df_test.shape)
df_test.head()

In [ ]:
model.load_state_dict(torch.load(checkpoint_path))
torch.save(model.state_dict(), model_path)

In [ ]:
# Load submission sample
submission = pd.read_csv(str(data_dir / "sample_submission.csv"))
print(submission.shape)

In [ ]:
model = SimpleNetwork(X.shape[1] * X.shape[2], y.shape[1])
model = model.to(device)
model.load_state_dict(torch.load(model_path))

In [ ]:
X, _ = extract_features(df_test, train = False)

X = torch.Tensor(X)

loader_test = DataLoader(X, batch_size = batch_size, shuffle = False)

In [ ]:
model.eval()  # 신경망을 추론 모드로 전환

# 데이터로더에서 미니배치를 하나씩 꺼내 추론을 수행
predict = []
with torch.no_grad():  # 추론 과정에는 미분이 필요없음
    for data in loader_test:
        data = data.to(device)

        outputs = model(data)  # 데이터를 입력하고 출력을 계산
        predict.append(outputs)
predict = torch.cat(predict, axis = 0).to('cpu')

In [ ]:
predict.shape

In [ ]:
print(submission.shape)
submission.columns

In [ ]:
submission['latDeg'] = predict[:,1]
submission['lngDeg'] = predict[:,2]

In [ ]:
submission.to_csv(f"./models/{notebookName}/{num_files} - result.csv", index = False)
pd.DataFrame([]).to_csv(dummy_path)